In [190]:
import pandas as pd
import numpy as np
import matplotlib.cm as cm
import matplotlib.colors as colors

!pip install geopandas==0.8.0
!pip install geojsonio==0.0.3

import geopandas as gpd


In [191]:
!conda install -c conda-forge folium=0.11.0 --yes
import folium

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.3
  latest version: 4.8.4

Please update conda by running

    $ conda update -n base -c defaults conda



# All requested packages already installed.



In [192]:
coviddata = "https://c19downloads.azureedge.net/downloads/msoa_data/MSOAs_latest.csv"
dfCovid = pd.read_csv(coviddata, index_col='msoa11_cd')
dfCovid.head()

rgn19_cd rgn19_nm  utla19_cd             utla19_nm   lad19_cd  \
msoa11_cd                                                                   
E02000001  E12000007   London  E09000001        City of London  E09000001   
E02000002  E12000007   London  E09000002  Barking and Dagenham  E09000002   
E02000003  E12000007   London  E09000002  Barking and Dagenham  E09000002   
E02000004  E12000007   London  E09000002  Barking and Dagenham  E09000002   
E02000005  E12000007   London  E09000002  Barking and Dagenham  E09000002   

                       lad19_nm         msoa11_hclnm  wk_05  wk_06  wk_07  \
msoa11_cd                                                                   
E02000001        City of London       City of London    NaN    NaN    NaN   
E02000002  Barking and Dagenham           Marks Gate    NaN    NaN    NaN   
E02000003  Barking and Dagenham  Chadwell Heath East    NaN    NaN    NaN   
E02000004  Barking and Dagenham         Eastbrookend    NaN    NaN    NaN   
E02000005  Barking and Dagenham      Becontree Heath    NaN    NaN    NaN   

           ...  wk_24  wk_25  wk_26  wk_27  wk_28  wk_29  wk_30  wk_31  wk_32  \
msoa11_cd  ...                                                                  
E02000001  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
E02000002  ...    NaN    NaN    NaN    NaN    NaN    NaN    3.0    NaN    NaN   
E02000003  ...    NaN    NaN    NaN    NaN    NaN    NaN    6.0    NaN    4.0   
E02000004  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
E02000005  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

           last_7_days  
msoa11_cd               
E02000001          NaN  
E02000002          NaN  
E02000003          4.0  
E02000004          NaN  
E02000005          NaN  

[5 rows x 36 columns]

In [193]:
dfCovid = dfCovid[['msoa11_hclnm','lad19_nm','last_7_days']]
dfCovid['last_7_days'] = dfCovid['last_7_days'].fillna(0)
dfCovid = dfCovid.reset_index()
dfCovid.rename(columns={'msoa11_cd':'MSOA01CD','msoa11_hclnm':'MSOA name','lad19_nm':'District','latest_7_days':'Infections (last 7 days)'}, inplace=True)
dfCovid.head()

MSOA01CD            MSOA name              District  last_7_days
0  E02000001       City of London        City of London          0.0
1  E02000002           Marks Gate  Barking and Dagenham          0.0
2  E02000003  Chadwell Heath East  Barking and Dagenham          4.0
3  E02000004         Eastbrookend  Barking and Dagenham          0.0
4  E02000005      Becontree Heath  Barking and Dagenham          0.0

In [194]:
pd.set_option('display.max_rows', None)
dfCovid.head()

MSOA01CD            MSOA name              District  last_7_days
0  E02000001       City of London        City of London          0.0
1  E02000002           Marks Gate  Barking and Dagenham          0.0
2  E02000003  Chadwell Heath East  Barking and Dagenham          4.0
3  E02000004         Eastbrookend  Barking and Dagenham          0.0
4  E02000005      Becontree Heath  Barking and Dagenham          0.0

*Noticed that one row is used to declare infections which are not attributed to a particular MSOA. This data is not relevant to my project as it cannot be displayed on a map of England. Further, it cannot be used to inform the lockdown of any establishment by geography. Code below removes this row and any others that might be lurking - in the end, just this one.*

In [195]:
dfCovid.drop(dfCovid[dfCovid['MSOA name'] == 'unallocated'].index, inplace = True)
dfCovid.shape

(6791, 4)

*The dataload was so heavy on memory that I needed to scale back my project to focus on one city area: Sheffield.*

In [196]:
pd.set_option('display.max_rows', None)
dfCovidSheffield = dfCovid[(dfCovid['District'] == 'Sheffield')]
dfCovidSheffield.head()

MSOA01CD                      MSOA name   District  last_7_days
1572  E02001611                   Stocksbridge  Sheffield          0.0
1573  E02001612         Deepcar & Bolsterstone  Sheffield          0.0
1574  E02001613         High Green & Burncross  Sheffield          0.0
1575  E02001614                     Chapeltown  Sheffield          0.0
1576  E02001615  Grenoside & Ecclesfield North  Sheffield          0.0

In [223]:
dfCovidSheffield.shape

(70, 4)

Using an API with the Office of National Statistics, I can access the geojson file containing boundary data for each MSOA. Notice that the codes for each MSOA (below) match those in the Covid table (above).

In [198]:
uk_geo = gpd.read_file('https://opendata.arcgis.com/datasets/7923d7e44c394653b3ba794699d50854_0.geojson')


DEBUG:fiona.env:Entering env context: <fiona.env.Env object at 0x7fbe95c84710>
DEBUG:fiona.env:Starting outermost env
DEBUG:fiona.env:No GDAL environment exists
DEBUG:fiona.env:New GDAL environment <fiona._env.GDALEnv object at 0x7fbe95b32940> created
DEBUG:fiona._env:Logging error handler pushed.
DEBUG:fiona._env:All drivers registered.
DEBUG:fiona._env:GDAL_DATA found in environment: '/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/fiona/gdal_data'.
DEBUG:fiona._env:PROJ_LIB found in environment: '/home/jupyterlab/conda/envs/python/share/proj'.
DEBUG:fiona._env:Started GDALEnv <fiona._env.GDALEnv object at 0x7fbe95b32940>.
DEBUG:fiona.env:Updated existing <fiona._env.GDALEnv object at 0x7fbe95b32940> with options {}
DEBUG:fiona.env:Entered env context: <fiona.env.Env object at 0x7fbe95c84710>
DEBUG:fiona._shim:Set option b'ENCODING': b'UTF-8'
DEBUG:fiona.ogrext:Got coordinate system
DEBUG:fiona.ogrext:Index: 0
DEBUG:fiona.collection:Flushed buffer
DEBUG:fiona.collectio

In [224]:
sheffield_geo = uk_geo[uk_geo['MSOA01NM'].str.contains('Sheffield')]
sheffield_geo.head()

OBJECTID   MSOA01CD       MSOA01NM      MSOA01NMW   Shape__Area  \
1610      1611  E02001611  Sheffield 001  Sheffield 001  5.717854e+06   
1611      1612  E02001612  Sheffield 002  Sheffield 002  1.331386e+07   
1612      1613  E02001613  Sheffield 003  Sheffield 003  4.273994e+06   
1613      1614  E02001614  Sheffield 004  Sheffield 004  5.321935e+06   
1614      1615  E02001615  Sheffield 005  Sheffield 005  1.109162e+07   

      Shape__Length                                           geometry  
1610   15167.789019  POLYGON ((-1.59042 53.47558, -1.59024 53.47529...  
1611   23325.723595  POLYGON ((-1.59024 53.47529, -1.59042 53.47558...  
1612   13505.526379  POLYGON ((-1.47423 53.46789, -1.47485 53.46779...  
1613   13660.654057  POLYGON ((-1.48012 53.45705, -1.48011 53.45723...  
1614   24251.369538  POLYGON ((-1.51492 53.46213, -1.51502 53.46233...

In [225]:
dfmerged = sheffield_geo.merge(dfCovidSheffield,on='MSOA01CD',how='left')
dfSheffield = dfmerged.dropna()
dfSheffield.head()


OBJECTID   MSOA01CD       MSOA01NM      MSOA01NMW   Shape__Area  \
0      1611  E02001611  Sheffield 001  Sheffield 001  5.717854e+06   
1      1612  E02001612  Sheffield 002  Sheffield 002  1.331386e+07   
2      1613  E02001613  Sheffield 003  Sheffield 003  4.273994e+06   
3      1614  E02001614  Sheffield 004  Sheffield 004  5.321935e+06   
4      1615  E02001615  Sheffield 005  Sheffield 005  1.109162e+07   

   Shape__Length                                           geometry  \
0   15167.789019  POLYGON ((-1.59042 53.47558, -1.59024 53.47529...   
1   23325.723595  POLYGON ((-1.59024 53.47529, -1.59042 53.47558...   
2   13505.526379  POLYGON ((-1.47423 53.46789, -1.47485 53.46779...   
3   13660.654057  POLYGON ((-1.48012 53.45705, -1.48011 53.45723...   
4   24251.369538  POLYGON ((-1.51492 53.46213, -1.51502 53.46233...   

                       MSOA name   District  last_7_days  
0                   Stocksbridge  Sheffield          0.0  
1         Deepcar & Bolsterstone  Sheffield          0.0  
2         High Green & Burncross  Sheffield          0.0  
3                     Chapeltown  Sheffield          0.0  
4  Grenoside & Ecclesfield North  Sheffield          0.0

In [201]:
#MSOA_name = dfCovidSheffield['MSOA name']
#sheffield_geo = sheffield_geo.join(MSOA_name)
#infections = dfCovidSheffield['Infections (last 7 days)']
#sheffield_geo = sheffield_geo.join(infections)
#sheffield_geo

In [202]:
#dfSheffieldmerged = pd.merge(dfCovidSheffield, sheffield_geo, on='MSOA01CD')
#dfSheffieldmerged
#pd.set_option('display.max_rows', None)
#dfSheffieldmerged.to_json(r'c:\\Users\epjac\Downloads\merged.json')

In [203]:
#dfSheffieldmerged = pd.concat([dfCovidSheffield, sheffield_geo], axis=1).to_json()

In [226]:
import folium
from folium import plugins
uk_map = folium.Map(location=[53.3831, -1.4645], zoom_start=11)
choropleth = folium.Choropleth(
    name='Sheffield Covid Data',
    geo_data=dfSheffield,
    data= dfSheffield,
    columns=['MSOA01CD','last_7_days'],
    key_on='feature.properties.MSOA01CD',
    fill_color='YlOrRd', 
    fill_opacity=0.4, 
    line_opacity=0.5,
    legend_name='SHEFFIELD - Covid infections in last 7 days',
    highlight=True
).add_to(uk_map)

choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['MSOA name','last_7_days'])
)

uk_map


## Importing, cleaning and preparing state schools' data, leaving school name, postcode and inspection Rating.

Inspection ratings: 1 - Outstanding, 2 - Good, 3 - Requires Improvement, 4 - Inadequate

In [205]:
dfSchools = pd.read_csv(r'https://assets.publishing.service.gov.uk/government/uploads/system/uploads/attachment_data/file/907735/Management_information_-_state-funded_schools_-_latest_inspections_at_31_July_2020.csv', header=0, low_memory=False, encoding='latin-1')
dfSchools.head()
#dirty data

Web link     URN  LAESTAB  \
0  http://www.ofsted.gov.uk/inspection-reports/fi...  100000  2013614   
1  http://www.ofsted.gov.uk/inspection-reports/fi...  100005  2021048   
2  http://www.ofsted.gov.uk/inspection-reports/fi...  100006  2021100   
3  http://www.ofsted.gov.uk/inspection-reports/fi...  100007  2021101   
4  http://www.ofsted.gov.uk/inspection-reports/fi...  100008  2022019   

                                 School name Ofsted phase  \
0  Sir John Cass's Foundation Primary School      Primary   
1                        Thomas Coram Centre      Nursery   
2                       CCfL Key Stage 4 PRU          PRU   
3         Camden Primary Pupil Referral Unit          PRU   
4                      Argyle Primary School      Primary   

        Type of education School open date Admissions policy  \
0  Voluntary Aided School              NaN    Not applicable   
1       LA Nursery School              NaN    Not applicable   
2     Pupil Referral Unit       01/09/1999    Not applicable   
3     Pupil Referral Unit              NaN    Not applicable   
4        Community School              NaN    Not applicable   

                   Sixth form Designated religious character  ...  \
0  Does not have a sixth form              Church of England  ...   
1              Not applicable                 Does not apply  ...   
2              Not applicable                 Does not apply  ...   
3              Not applicable                 Does not apply  ...   
4  Does not have a sixth form                 Does not apply  ...   

  School type at time of previous full inspection  \
0                          Voluntary Aided School   
1                               LA Nursery School   
2                             Pupil Referral Unit   
3                             Pupil Referral Unit   
4                                Community School   

  Previous full inspection overall effectiveness Previous category of concern  \
0                                            1.0                          NaN   
1                                            1.0                          NaN   
2                                            2.0                          NaN   
3                                            2.0                          NaN   
4                                            2.0                          NaN   

  Previous quality of education Previous behaviour and attitudes  \
0                           9.0                              9.0   
1                           9.0                              9.0   
2                           9.0                              9.0   
3                           9.0                              9.0   
4                           9.0                              9.0   

  Previous personal development  \
0                           9.0   
1                           9.0   
2                           9.0   
3                           9.0   
4                           9.0   

  Previous effectiveness of leadership and management  \
0                                                1.0    
1                                                1.0    
2                                                2.0    
3                                                2.0    
4                                                2.0    

   Previous safeguarding is effective?  \
0                                    9   
1                                    9   
2                                    9   
3                                    9   
4                                    9   

   Previous early years provision (where applicable)  \
0                                                1.0   
1                                                1.0   
2                                                9.0   
3                                                9.0   
4                                                2.0   

   Previous sixth form provision (where applicable)  
0                        

In [228]:
dfSheffield = dfSchools[(dfSchools['Local authority'] == 'Sheffield')]
dfSheffield = dfSheffield[['URN','School name','Postcode','Overall effectiveness']]
dfSheffield['Postcode'] = dfSheffield['Postcode'].str.replace(' ','') # remove space inside postcodes to avoid API error
dfSheffield = dfSheffield.dropna() # remove rows with missing values (2 new academy converters without inspection ratings)
dfSheffield.head()

URN                           School name Postcode  \
3179  106973              Broomhall Nursery School   S102DN   
3180  106975             Grace Owen Nursery School    S25QD   
3181  106982             Abbey Lane Primary School    S80BN   
3182  106987  Brightside Nursery and Infant School    S91AS   
3183  106988           Carter Knowle Junior School    S72DY   

      Overall effectiveness  
3179                    1.0  
3180                    2.0  
3181                    2.0  
3182                    1.0  
3183                    2.0

In [207]:
!pip install geocoder
import geocoder

In [229]:
#A slow API loop but tried many other possibilities to get to this point including api.postcodes.io
def get_latlng(arcgis_geocoder):
    lat_lng_coords = None
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Sheffield, United Kingdom'.format(arcgis_geocoder))
        lat_lng_coords = g.latlng
    return lat_lng_coords

postal_codes = dfSheffield['Postcode']    
coordinates = [get_latlng(postal_code) for postal_code in postal_codes.tolist()]

dflatlang = pd.DataFrame(coordinates, columns = ['Latitude', 'Longitude'])

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): geocode.arcgis.com:443
DEBUG:urllib3.connectionpool:https://geocode.arcgis.com:443 "GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S102DN%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1" 200 230
INFO:geocoder.base:Requested https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find?f=json&text=S102DN%2C+Sheffield%2C+United+Kingdom&maxLocations=1
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): geocode.arcgis.com:443


send: b'GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S102DN%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1\r\nHost: geocode.arcgis.com\r\nUser-Agent: python-requests/2.24.0\r\nAccept-Encoding: gzip, deflate\r\nAccept: */*\r\nConnection: keep-alive\r\n\r\n'
reply: 'HTTP/1.1 200 \r\n'
header: Date: Thu, 20 Aug 2020 13:29:02 GMT
header: Content-Type: application/json;charset=UTF-8
header: Content-Length: 230
header: Connection: keep-alive
header: X-Content-Type-Options: nosniff
header: X-XSS-Protection: 1; mode=block
header: Server: 
header: ETag: 9d12368e
header: x-esri-ftiles-cache-compress: true
header: Content-Encoding: gzip
header: Cache-Control: max-age=300
header: X-Cached: MISS
header: Vary: Origin,Accept-Encoding
send: b'GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S25QD%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1\r\nHost: geocode.arcgis.com\r\nUser-Agent: python-requests/2.24.0\r\nAccept-Encoding: gzip, deflate\r\nAccept: */

DEBUG:urllib3.connectionpool:https://geocode.arcgis.com:443 "GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S25QD%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1" 200 230
INFO:geocoder.base:Requested https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find?f=json&text=S25QD%2C+Sheffield%2C+United+Kingdom&maxLocations=1
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): geocode.arcgis.com:443


reply: 'HTTP/1.1 200 \r\n'
header: Date: Thu, 20 Aug 2020 13:29:03 GMT
header: Content-Type: application/json;charset=UTF-8
header: Content-Length: 230
header: Connection: keep-alive
header: X-Content-Type-Options: nosniff
header: X-XSS-Protection: 1; mode=block
header: Server: 
header: ETag: 3bb0f728
header: x-esri-ftiles-cache-compress: true
header: Content-Encoding: gzip
header: Cache-Control: max-age=300
header: X-Cached: MISS
header: Vary: Origin,Accept-Encoding
send: b'GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S80BN%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1\r\nHost: geocode.arcgis.com\r\nUser-Agent: python-requests/2.24.0\r\nAccept-Encoding: gzip, deflate\r\nAccept: */*\r\nConnection: keep-alive\r\n\r\n'


DEBUG:urllib3.connectionpool:https://geocode.arcgis.com:443 "GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S80BN%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1" 200 230
INFO:geocoder.base:Requested https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find?f=json&text=S80BN%2C+Sheffield%2C+United+Kingdom&maxLocations=1
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): geocode.arcgis.com:443


...

reply: 'HTTP/1.1 200 \r\n'
header: Date: Thu, 20 Aug 2020 13:30:41 GMT
header: Content-Type: application/json;charset=UTF-8
header: Content-Length: 229
header: Connection: keep-alive
header: X-Content-Type-Options: nosniff
header: X-XSS-Protection: 1; mode=block
header: Server: 
header: ETag: dcaab19c
header: x-esri-ftiles-cache-compress: true
header: Content-Encoding: gzip
header: Cache-Control: max-age=300
header: X-Cached: MISS
header: Vary: Origin,Accept-Encoding
send: b'GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S48HQ%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1\r\nHost: geocode.arcgis.com\r\nUser-Agent: python-requests/2.24.0\r\nAccept-Encoding: gzip, deflate\r\nAccept: */*\r\nConnection: keep-alive\r\n\r\n'


DEBUG:urllib3.connectionpool:https://geocode.arcgis.com:443 "GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S48HQ%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1" 200 228
INFO:geocoder.base:Requested https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find?f=json&text=S48HQ%2C+Sheffield%2C+United+Kingdom&maxLocations=1
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): geocode.arcgis.com:443


reply: 'HTTP/1.1 200 \r\n'
header: Date: Thu, 20 Aug 2020 13:30:41 GMT
header: Content-Type: application/json;charset=UTF-8
header: Content-Length: 228
header: Connection: keep-alive
header: X-Content-Type-Options: nosniff
header: X-XSS-Protection: 1; mode=block
header: Server: 
header: ETag: d7ea305a
header: x-esri-ftiles-cache-compress: true
header: Content-Encoding: gzip
header: Cache-Control: max-age=300
header: X-Cached: EXPIRED
header: Vary: Origin,Accept-Encoding
send: b'GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S350AE%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1\r\nHost: geocode.arcgis.com\r\nUser-Agent: python-requests/2.24.0\r\nAccept-Encoding: gzip, deflate\r\nAccept: */*\r\nConnection: keep-alive\r\n\r\n'


DEBUG:urllib3.connectionpool:https://geocode.arcgis.com:443 "GET /arcgis/rest/services/World/GeocodeServer/find?f=json&text=S350AE%2C+Sheffield%2C+United+Kingdom&maxLocations=1 HTTP/1.1" 200 229
INFO:geocoder.base:Requested https://geocode.arcgis.com/arcgis/rest/services/World/GeocodeServer/find?f=json&text=S350AE%2C+Sheffield%2C+United+Kingdom&maxLocations=1


reply: 'HTTP/1.1 200 \r\n'
header: Date: Thu, 20 Aug 2020 13:30:41 GMT
header: Content-Type: application/json;charset=UTF-8
header: Content-Length: 229
header: Connection: keep-alive
header: X-Content-Type-Options: nosniff
header: X-XSS-Protection: 1; mode=block
header: Server: 
header: ETag: 179cbbb4
header: x-esri-ftiles-cache-compress: true
header: Content-Encoding: gzip
header: Cache-Control: max-age=300
header: X-Cached: MISS
header: Vary: Origin,Accept-Encoding


In [230]:
dfSheffieldlatlang = dfSheffield.reset_index() #index reset as lat and lang data appears as Nan in dfSheffield but not in dflatlang - not sure why
dfSheffieldlatlang['Latitude'] = dflatlang['Latitude']
dfSheffieldlatlang['Longitude'] = dflatlang['Longitude']
dfSheffieldlatlang.head()

index     URN                           School name Postcode  \
0   3179  106973              Broomhall Nursery School   S102DN   
1   3180  106975             Grace Owen Nursery School    S25QD   
2   3181  106982             Abbey Lane Primary School    S80BN   
3   3182  106987  Brightside Nursery and Infant School    S91AS   
4   3183  106988           Carter Knowle Junior School    S72DY   

   Overall effectiveness  Latitude  Longitude  
0                    1.0  53.37449   -1.48654  
1                    2.0  53.38178   -1.45873  
2                    2.0  53.33886   -1.48590  
3                    1.0  53.41179   -1.42042  
4                    2.0  53.35231   -1.49390

In [231]:


# add the schools as blue circle markers
for lat, lng, label in zip(dfSheffieldlatlang['Latitude'], dfSheffieldlatlang['Longitude'], dfSheffieldlatlang['School name']):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(uk_map)

# display map
uk_map

In [211]:
!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim

from pandas.io.json import json_normalize

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.3
  latest version: 4.8.4

Please update conda by running

    $ conda update -n base -c defaults conda



# All requested packages already installed.



In [212]:
CLIENT_ID = 'N2S5UBGK4NIB1EPVH3YROKUG4K3NAV1WVGSTBANDT1POTFAZ' # your Foursquare ID
CLIENT_SECRET = 'JSJX1ROMN1GBLZTH3PSQRYCMCAFUHD2FD13BJCH50XWZSWFW' # your Foursquare Secret
VERSION = '20200813'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: N2S5UBGK4NIB1EPVH3YROKUG4K3NAV1WVGSTBANDT1POTFAZ
CLIENT_SECRET:JSJX1ROMN1GBLZTH3PSQRYCMCAFUHD2FD13BJCH50XWZSWFW


In [213]:
address = 'Sheffield, United Kingdom'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print(latitude, longitude)

DEBUG:urllib3.util.retry:Converted retries value: 2 -> Retry(total=2, connect=None, read=None, redirect=None, status=None)
DEBUG:urllib3.util.retry:Converted retries value: 2 -> Retry(total=2, connect=None, read=None, redirect=None, status=None)
DEBUG:geopy:Nominatim.geocode: https://nominatim.openstreetmap.org/search?q=Sheffield%2C+United+Kingdom&format=json&limit=1
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): nominatim.openstreetmap.org:443
DEBUG:urllib3.connectionpool:https://nominatim.openstreetmap.org:443 "GET /search?q=Sheffield%2C+United+Kingdom&format=json&limit=1 HTTP/1.1" 200 None


send: b'GET /search?q=Sheffield%2C+United+Kingdom&format=json&limit=1 HTTP/1.1\r\nHost: nominatim.openstreetmap.org\r\nUser-Agent: foursquare_agent\r\nAccept-Encoding: gzip, deflate\r\nAccept: */*\r\nConnection: keep-alive\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: nginx
header: Date: Thu, 20 Aug 2020 13:21:23 GMT
header: Content-Type: application/json; charset=UTF-8
header: Transfer-Encoding: chunked
header: Connection: keep-alive
header: Keep-Alive: timeout=20
header: Access-Control-Allow-Origin: *
header: Access-Control-Allow-Methods: OPTIONS,GET
53.3806626 -1.4702278


In [214]:
search_query = 'football&club'
radius = 5000
print(search_query + ' .... OK!')

football&club .... OK!


In [215]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=N2S5UBGK4NIB1EPVH3YROKUG4K3NAV1WVGSTBANDT1POTFAZ&client_secret=JSJX1ROMN1GBLZTH3PSQRYCMCAFUHD2FD13BJCH50XWZSWFW&ll=53.3806626,-1.4702278&v=20200813&query=football&club&radius=5000&limit=30'

In [232]:
results = requests.get(url).json()
venues = results['response']['venues']
sportslocs = json_normalize(venues)
sportslocs

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): api.foursquare.com:443
DEBUG:urllib3.connectionpool:https://api.foursquare.com:443 "GET /v2/venues/search?client_id=N2S5UBGK4NIB1EPVH3YROKUG4K3NAV1WVGSTBANDT1POTFAZ&client_secret=JSJX1ROMN1GBLZTH3PSQRYCMCAFUHD2FD13BJCH50XWZSWFW&ll=53.3806626,-1.4702278&v=20200813&query=football&club&radius=5000&limit=30 HTTP/1.1" 200 None


send: b'GET /v2/venues/search?client_id=N2S5UBGK4NIB1EPVH3YROKUG4K3NAV1WVGSTBANDT1POTFAZ&client_secret=JSJX1ROMN1GBLZTH3PSQRYCMCAFUHD2FD13BJCH50XWZSWFW&ll=53.3806626,-1.4702278&v=20200813&query=football&club&radius=5000&limit=30 HTTP/1.1\r\nHost: api.foursquare.com\r\nUser-Agent: python-requests/2.24.0\r\nAccept-Encoding: gzip, deflate\r\nAccept: */*\r\nConnection: keep-alive\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Connection: keep-alive
header: Server: nginx
header: Content-Type: application/json; charset=utf-8
header: Tracer-Time: 51
header: X-RateLimit-Path: /v2/venues/search
header: X-RateLimit-Limit: 5000
header: X-RateLimit-Reset: 1597934580
header: X-RateLimit-Remaining: 4999
header: Access-Control-Allow-Origin: *
header: Strict-Transport-Security: max-age=31536000
header: X-Rate-Limit-Key: 158.85.69.121
header: X-ex: fastly_cdn
header: Content-Encoding: gzip
header: Accept-Ranges: bytes
header: Date: Thu, 20 Aug 2020 13:43:31 GMT
header: Via: 1.1 varnish
header: X-Served-

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


id                          name  \
0  4fae5f5de4b047f11d1af88f  Old Abandoned Football Pitch   
1  4b8faa73f964a520185c33e3                  Bramall Lane   
2  532ec9f1498e69d80d9e757b    Nether Green Football Club   
3  4b6a082bf964a520fac22be3          Hillsborough Stadium   

                                          categories    referralId  hasPerk  \
0  [{'id': '4cce455aebf7b749d5e191f5', 'name': 'S...  v-1597931011    False   
1  [{'id': '4bf58dd8d48988d188941735', 'name': 'S...  v-1597931011    False   
2  [{'id': '4cce455aebf7b749d5e191f5', 'name': 'S...  v-1597931011    False   
3  [{'id': '4bf58dd8d48988d188941735', 'name': 'S...  v-1597931011    False   

   location.lat  location.lng  \
0     53.370495     -1.486955   
1     53.370285     -1.470795   
2     53.353385     -1.536149   
3     53.411386     -1.500707   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 53.37049521368912...               1585   
1  [{'label': 'display', 'lat': 53.37028458665696...               1155   
2  [{'label': 'display', 'lat': 53.35338490717388...               5328   
3  [{'label': 'display', 'lat': 53.41138646877157...               3973   

  location.cc location.city location.state location.country  \
0          GB     Sheffield      Sheffield   United Kingdom   
1          GB     Sheffield            NaN   United Kingdom   
2          GB     Sheffield      Sheffield   United Kingdom   
3          GB     Sheffield            NaN   United Kingdom   

                           location.formattedAddress location.address  \
0                        [Sheffield, United Kingdom]              NaN   
1    [Bramall Ln, Sheffield, S2 4SU, United Kingdom]       Bramall Ln   
2           [Common Lane, Sheffield, United Kingdom]      Common Lane   
3  [Penistone Rd, Sheffield, S6 1SW, United Kingdom]     Penistone Rd   

  location.postalCode  
0                 NaN  
1              S2 4SU  
2                 NaN  
3              S6 1SW

In [233]:
sportslocs = sportslocs.drop(sportslocs.index[[0,2]])
sportslocs

id                  name  \
1  4b8faa73f964a520185c33e3          Bramall Lane   
3  4b6a082bf964a520fac22be3  Hillsborough Stadium   

                                          categories    referralId  hasPerk  \
1  [{'id': '4bf58dd8d48988d188941735', 'name': 'S...  v-1597931011    False   
3  [{'id': '4bf58dd8d48988d188941735', 'name': 'S...  v-1597931011    False   

   location.lat  location.lng  \
1     53.370285     -1.470795   
3     53.411386     -1.500707   

                             location.labeledLatLngs  location.distance  \
1  [{'label': 'display', 'lat': 53.37028458665696...               1155   
3  [{'label': 'display', 'lat': 53.41138646877157...               3973   

  location.cc location.city location.state location.country  \
1          GB     Sheffield            NaN   United Kingdom   
3          GB     Sheffield            NaN   United Kingdom   

                           location.formattedAddress location.address  \
1    [Bramall Ln, Sheffield, S2 4SU, United Kingdom]       Bramall Ln   
3  [Penistone Rd, Sheffield, S6 1SW, United Kingdom]     Penistone Rd   

  location.postalCode  
1              S2 4SU  
3              S6 1SW

In [237]:
for lat, lng, label in zip(sportslocs['location.lat'], sportslocs['location.lng'], sportslocs['name']):
    folium.Marker(
        [lat, lng],
        popup=label,
        fill = True,
        icon=folium.Icon(color='green'), #wanted different colour for marker
        fill_opacity=0.6
    ).add_to(uk_map)

# display map
uk_map